# MY FINAL CAPSTONE PROJECT

## I will compare the cities of New York (USA) and Toronto (CAN) and analyse where we we have potential to open additional vegetarian/vegan restaurants.

**The libraries I am using:**

In [496]:
#!conda install -c conda-forge wikipedia --yes
#!conda install -c conda-forge folium --yes
#!conda install -c conda-forge geopy --yes

import folium
import wikipedia as wp
import numpy as np
import pandas as pd
import requests
from lxml import html
from bs4 import BeautifulSoup
from tabulate import tabulate
import json
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt
from geopy.geocoders import Nominatim 

**First I load the data of New York and Toronto and omit duplicates.**

### New York:

In [497]:
!wget -q -O "newyork_data.json" https://ibm.box.com/shared/static/fbpwbovar7lf8p5sgddm06cgipa2rxpe.json
    
with open("newyork_data.json") as json_data:
    ny_data_raw_1 = json.load(json_data)  
    

ny_data_raw_2 = ny_data_raw_1["features"]
ny_df = pd.DataFrame(columns = [ 'Borough', 'Neighbourhood', 'Latitude', 'Longitude'])

for data in ny_data_raw_2:
    borough = ny_df_name = data['properties']['borough'] 
    ny_df_name = data['properties']['name']
        
    ny_df_latlon = data['geometry']['coordinates']
    ny_df_lat = ny_df_latlon[1]
    ny_df_lon = ny_df_latlon[0]
    
    ny_df = ny_df.append({'Borough': borough,
                                          'Neighbourhood': ny_df_name,
                                          'Latitude': ny_df_lat,
                                          'Longitude': ny_df_lon}, ignore_index=True)   

print("The New York data contains {} rows.".format(ny_df.shape[0]))
ny_df.drop_duplicates("Neighbourhood", inplace = True)
print("After removing the duplicates, the New York data contains {} rows.".format(ny_df.shape[0]))

The New York data contains 306 rows.
After removing the duplicates, the New York data contains 302 rows.


### Toronto:

In [498]:
html = wp.page("List of postal codes of Canada: M").html().encode("UTF-8")

to_df = pd.read_html(html, header = 0)[0]
to_df = to_df[to_df.Borough != "Not assigned"]
to_df = to_df[to_df["Borough"].str.contains("Toronto")].reset_index(drop = True)

In the following cell I download the data for the spatial coordinates of the post codess, but since it accesses a file in my IBM Cloud Object Storage it includes my credentials, which are not to be shown.

In [499]:
# The code was removed by Watson Studio for sharing.

**I again remove duplicates, furthermore I drop the data for the Postcodes, since we do not need it anymore.**

In [500]:
to_df = to_df.join(spatial_data, on = "Postcode")

print("The Toronto data contains {} rows.".format(to_df.shape[0]))
to_df.drop_duplicates("Postcode", inplace = True)
print("After removing the duplicates, the Toronto data contains {} rows.".format(to_df.shape[0]))
to_df.drop(["Postcode"], axis = 1, inplace = True)

The Toronto data contains 74 rows.
After removing the duplicates, the Toronto data contains 39 rows.


### Here I map the neighbourhoods of Toronto

In [501]:
address = 'Toronto, Ontario Canada'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighbourhood in zip(to_df['Latitude'], to_df['Longitude'], to_df['Borough'], to_df['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_toronto)
map_toronto

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.21.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


### Here I map the neighbourhoods of New York

In [502]:
address = 'New York, NY'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
map_ny = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighbourhood in zip(ny_df['Latitude'], ny_df['Longitude'], ny_df['Borough'], ny_df['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_ny)
map_ny

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.21.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


**The next step is importing data from foursquare. The credentials are, again hidden. We will request data from the website to analyse it.**

In [503]:
# The code was removed by Watson Studio for sharing.

In [504]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, return_text = False):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        
        if return_text == True:
            print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
            
    return(nearby_venues)

In [505]:
# The code was removed by Watson Studio for sharing.

### Here I take the locational data of all the Venus that contain the string "Restaurant" or "Place". Furthermore I divide the dataframe into a total and a vegetarian/vegan dataframe.

In [506]:
to_restaurants = to_venues[to_venues["Venue Category"].str.contains("Restaurant" or "Place")].reset_index(drop = True)
to_restaurants_veg = to_restaurants[to_restaurants["Venue Category"].str.contains("Veg")].reset_index(drop = True)

ny_restaurants = ny_venues[ny_venues["Venue Category"].str.contains("Restaurant" or "Place")].reset_index(drop = True)
ny_restaurants_veg = ny_restaurants[ny_restaurants["Venue Category"].str.contains("Veg")].reset_index(drop = True)

### This is how the data frame for Toronto looks like

In [507]:
to_restaurants_veg

Neighbourhood  Neighbourhood Latitude  \
0                    St. James Town               43.651494   
1                       Berczy Park               43.644771   
2                Central Bay Street               43.657952   
3                          Adelaide               43.650571   
4                          Adelaide               43.650571   
5                 Harbourfront East               43.640816   
6                   Little Portugal               43.647927   
7                   Design Exchange               43.647177   
8                    Commerce Court               43.648198   
9                    Commerce Court               43.648198   
10                        The Annex               43.672710   
11                        Runnymede               43.651571   
12                        Chinatown               43.653206   
13                        Chinatown               43.653206   
14                        Chinatown               43.653206   
15  Stn A PO Boxes 25 The Esplanade               43.646435   
16             First Canadian Place               43.648429   

    Neighbourhood Longitude                  Venue  Venue Latitude  \
0                -79.375418         Fresh On Front       43.647815   
1                -79.373306         Fresh On Front       43.647815   
2                -79.387383       Vegetarian Haven       43.656016   
3                -79.384568              Rosalinda       43.650252   
4                -79.384568           Planta Queen       43.650622   
5                -79.381752          Kupfert & Kim       43.641179   
6                -79.419750              The Goods       43.649259   
7                -79.381576              Rosalinda       43.650252   
8                -79.379817         Fresh On Front       43.647815   
9                -79.379817              Rosalinda       43.650252   
10               -79.405678  Live Organic Food Bar       43.675053   
11               -79.484450                   Awai       43.650412   
12               -79.400049               Hibiscus       43.655454   
13               -79.400049    Buddha's Vegetarian       43.651904   
14               -79.400049        Urban Herbivore       43.656193   
15               -79.374846         Fresh On Front       43.647815   
16               -79.382280              Rosalinda       43.650252   

    Venue Longitude                 Venue Category  
0        -79.374453  Vegetarian / Vegan Restaurant  
1        -79.374453  Vegetarian / Vegan Restaurant  
2        -79.392758  Vegetarian / Vegan Restaurant  
3        -79.385156  Vegetarian / Vegan Restaurant  
4        -79.388154  Vegetarian / Vegan Restaurant  
5        -79.378144  Vegetarian / Vegan Restaurant  
6        -79.424022  Vegetarian / Vegan Restaurant  
7        -79.385156  Vegetarian / Vegan Restaurant  
8        -79.374453  Vegetarian / Vegan Restaurant  
9        -79.385156  Vegetarian / Vegan Restaurant  
10       -79.406715  Vegetarian / Vegan Restaurant  
11       -79.478477  Vegetarian / Vegan Restaurant  
12       -79.402439  Vegetarian / Vegan Restaurant  
13       -79.403312  Vegetarian / Vegan Restaurant  
14       -79.402673  Vegetarian / Vegan Restaurant  
15       -79.374453  Vegetarian / Vegan Restaurant  
16       -79.385156  Vegetarian / Vegan Restaurant

### In New York we, of course, have more restaurants.

In [508]:
ny_restaurants_veg

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0          Greenpoint               40.730201               -73.954241   
1    Prospect Heights               40.676822               -73.964859   
2            Bushwick               40.698116               -73.925258   
3            Bushwick               40.698116               -73.925258   
4         Fort Greene               40.688527               -73.972906   
5        Coney Island               40.574293               -73.988683   
6        Clinton Hill               40.693229               -73.967843   
7   East Williamsburg               40.708492               -73.938858   
8   East Williamsburg               40.708492               -73.938858   
9          North Side               40.714823               -73.958809   
10         North Side               40.714823               -73.958809   
11    Upper East Side               40.775639               -73.960508   
12    Upper East Side               40.775639               -73.960508   
13         Lenox Hill               40.768113               -73.958860   
14    Upper West Side               40.787658               -73.977059   
15    Upper West Side               40.787658               -73.977059   
16            Clinton               40.759101               -73.996119   
17        Murray Hill               40.748303               -73.978332   
18            Chelsea               40.744035               -74.003116   
19  Greenwich Village               40.726933               -73.999914   
20       East Village               40.727847               -73.982226   
21       East Village               40.727847               -73.982226   
22       East Village               40.727847               -73.982226   
23            Tribeca               40.721522               -74.010683   
24       Little Italy               40.719324               -73.997305   
25               Soho               40.722184               -74.000657   
26               Soho               40.722184               -74.000657   
27            Astoria               40.768509               -73.915654   
28          Ridgewood               40.708323               -73.901435   
29      Fresh Meadows               40.734394               -73.782713   
30      South Jamaica               40.696911               -73.790426   
31     Rockaway Beach               40.582802               -73.822361   
32    Queensboro Hill               40.744572               -73.825809   
33           Grasmere               40.598268               -74.076674   
34      Carnegie Hill               40.782683               -73.953256   
35      Midtown South               40.748510               -73.988713   
36      Midtown South               40.748510               -73.988713   
37             Utopia               40.733500               -73.796717   
38       Sutton Place               40.760280               -73.963556   
39       Sutton Place               40.760280               -73.963556   
40           Flatiron               40.739673               -73.990947   
41           Flatiron               40.739673               -73.990947   
42              Malba               40.790602               -73.826678   

                             Venue  Venue Latitude  Venue Longitude  \
0                      Jungle Cafe       40.730201       -73.954761   
1                    Natural Blend       40.673819       -73.962923   
2                     Hartbreakers       40.701627       -73.922853   
3                         Sol Sips       40.699135       -73.922510   
4             LuAnne's Wild Ginger       40.689644       -73.969824   
5                 Marty’s V Burger       40.574932       -73.984353   
6             LuAnne's Wild Ginger       40.689644       -73.969824   
7                     Champs Diner       40.708335       -73.940816   
8                       Loving Hut       40.712549       -73.941106   
9                        by CHLOE.       

## Now we have all the tools we need to map all the restaurants in blue and vegetarian/vegan restaurants in green.

### First for Toronto:

In [509]:
address = 'Toronto, Ontario Canada'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, venue, neighbourhood in zip(to_restaurants['Venue Latitude'], to_restaurants['Venue Longitude'], to_restaurants['Venue'], to_restaurants['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, venue)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.2,
        parse_html=False).add_to(map_toronto)
    
for lat, lng, venue, neighbourhood in zip(to_restaurants_veg['Venue Latitude'], to_restaurants_veg['Venue Longitude'], to_restaurants_veg['Venue'], to_restaurants_veg['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, venue)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='green',
        fill=True,
        fill_color='#87face',
        fill_opacity=0.5,
        parse_html=False).add_to(map_toronto)


map_toronto

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.21.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


**In Toronto it is noteworthy that vegetarian/veganrestaurants seem to be concentrated and not spread out in the city, so there is much potential to open up a business!**

In [510]:
address = 'New York, NY'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
map_ny = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, venue, neighbourhood in zip(ny_restaurants['Venue Latitude'], ny_restaurants['Venue Longitude'], ny_restaurants['Venue'], ny_restaurants['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, venue)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.2,
        parse_html=False).add_to(map_ny)
    
for lat, lng, venue, neighbourhood in zip(ny_restaurants_veg['Venue Latitude'], ny_restaurants_veg['Venue Longitude'], ny_restaurants_veg['Venue'], ny_restaurants_veg['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, venue)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='green',
        fill=True,
        fill_color='#87face',
        fill_opacity=0.5,
        parse_html=False).add_to(map_ny)


map_ny

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.21.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  app.launch_new_instance()


**Manhattan seems to have a high restaurant density in general, but it is moteworthy how many vegetarian/vegan restaurants are in Manhattan. Staten Island has only 1 restaurant, Bronx not a single one and Queens and Brooklyn have just a few, so there much potential for more vegetarian/vegan restaurants.**

**To obtain numerical values di the following steps:**

In [511]:
to_df_analysis_allrest = to_restaurants[["Neighbourhood", "Venue Category"]]
ny_df_analysis_allrest = ny_restaurants[["Neighbourhood", "Venue Category"]]
to_df_analysis_vegrest = to_restaurants_veg[["Neighbourhood", "Venue Category"]]
ny_df_analysis_vegrest = ny_restaurants_veg[["Neighbourhood", "Venue Category"]]

In [512]:
to_rest_tot_data = to_df_analysis_allrest.groupby('Neighbourhood').count().reset_index(level = "Neighbourhood")
ny_rest_tot_data = ny_df_analysis_allrest.groupby('Neighbourhood').count().reset_index(level = "Neighbourhood")
to_rest_veg_data = to_df_analysis_vegrest.groupby('Neighbourhood').count().reset_index(level = "Neighbourhood")
ny_rest_veg_data = ny_df_analysis_vegrest.groupby('Neighbourhood').count().reset_index(level = "Neighbourhood")

### Here is how the dataframes for Toronto look like (first for all the restaurants, second for vegetarian/vegan restaurants:

In [513]:
to_rest_tot_data

Neighbourhood  Venue Category
0                                            Adelaide              28
1                                         Berczy Park              11
2                                            Brockton               3
3   Business Reply Mail Processing Centre 969 Eastern               2
4                                         Cabbagetown              11
5                                  Central Bay Street              22
6                                           Chinatown              27
7                                            Christie               2
8                                Church and Wellesley              28
9                                      Commerce Court              26
10                                         Davisville              10
11                                          Deer Park               4
12                                    Design Exchange              24
13                                 Dovercourt Village               1
14                               First Canadian Place              27
15                                  Forest Hill North               1
16                                            Harbord               9
17                                       Harbourfront               6
18                                  Harbourfront East              15
19                                          High Park               7
20                                    Little Portugal              18
21                                 North Toronto West               4
22                                           Parkdale               4
23                                       Queen's Park               9
24                                          Runnymede              10
25                                            Ryerson              22
26                                     St. James Town              21
27                    Stn A PO Boxes 25 The Esplanade              19
28                                    Studio District               9
29                                          The Annex               4
30                                   The Beaches West               2
31                                  The Danforth West              15

In [514]:
to_rest_veg_data

Neighbourhood  Venue Category
0                          Adelaide               2
1                       Berczy Park               1
2                Central Bay Street               1
3                         Chinatown               3
4                    Commerce Court               2
5                   Design Exchange               1
6              First Canadian Place               1
7                 Harbourfront East               1
8                   Little Portugal               1
9                         Runnymede               1
10                   St. James Town               1
11  Stn A PO Boxes 25 The Esplanade               1
12                        The Annex               1

### In less than a third of the Neighbourhoods we have a vegetarian/vegan restaurant!

**Now we create dataframes of the amount of total restaurants and vegetarian/vegan restaurants for each neighbourhood, to calculate the fraction of the latter.**

In [515]:
to_veg_list = []
ny_veg_list = []

i = 0
j = 0

while i < len(to_rest_tot_data["Neighbourhood"]):
    
    if j < (len(to_rest_veg_data["Neighbourhood"])):
          
        if to_rest_tot_data["Neighbourhood"][i] == to_rest_veg_data["Neighbourhood"][j]:
        
            to_veg_list.append(to_rest_veg_data["Venue Category"][j])
            j += 1
            i += 1
            
        else:
            
            to_veg_list.append(0)
            i +=1
    
    else:
        
        i+=1        
        to_veg_list.append(0)
        
 
i = 0
j = 0

while i < len(ny_rest_tot_data["Neighbourhood"]):
    
    if j < (len(ny_rest_veg_data["Neighbourhood"])):
          
        if ny_rest_tot_data["Neighbourhood"][i] == ny_rest_veg_data["Neighbourhood"][j]:
        
            ny_veg_list.append(ny_rest_veg_data["Venue Category"][j])
            j += 1
            i += 1
            
        else:
            
            ny_veg_list.append(0)
            i +=1
    
    else:
        
        i+=1        
        ny_veg_list.append(0)

### Here we concatenate the columns and create dataframes that contain all the data. Furthermore we calculate the percentage of vegetarian/vegan restaurants in each district.

In [516]:
to_veg_column = {"Vegetarian / Vegan Restaurants" : to_veg_list}
to_neighbourhood = to_rest_tot_data["Neighbourhood"]
to_num_rest = to_rest_tot_data["Venue Category"]
to_num_veg_rest = pd.DataFrame(to_veg_column)

to_eval_data = pd.concat([to_neighbourhood, to_num_rest, to_num_veg_rest], axis = 1, sort = False).rename(columns = {"Venue Category" : "Total Restaurants"})#.set_index("Neighbourhood")
to_eval_data["Percentage"] = round(to_eval_data["Vegetarian / Vegan Restaurants"] / to_eval_data["Total Restaurants"] * 100, 2)



ny_veg_column = {"Vegetarian / Vegan Restaurants" : ny_veg_list}
ny_neighbourhood = ny_rest_tot_data["Neighbourhood"]
ny_num_rest = ny_rest_tot_data["Venue Category"]
ny_num_veg_rest = pd.DataFrame(ny_veg_column)

ny_eval_data = pd.concat([ny_neighbourhood, ny_num_rest, ny_num_veg_rest], axis = 1, sort = False).rename(columns = {"Venue Category" : "Total Restaurants"})#.set_index("Neighbourhood")
ny_eval_data["Percentage"] = round(ny_eval_data["Vegetarian / Vegan Restaurants"] / ny_eval_data["Total Restaurants"] * 100, 2)

### Here are the best and worst places in Toronto to search for a vegetarian/vegan restaurant:

**Best:**

In [517]:
to_eval_data.sort_values(by = "Percentage", ascending = False).head(10)

Neighbourhood  Total Restaurants  \
29                        The Annex                  4   
6                         Chinatown                 27   
24                        Runnymede                 10   
1                       Berczy Park                 11   
9                    Commerce Court                 26   
0                          Adelaide                 28   
18                Harbourfront East                 15   
20                  Little Portugal                 18   
27  Stn A PO Boxes 25 The Esplanade                 19   
26                   St. James Town                 21   

    Vegetarian / Vegan Restaurants  Percentage  
29                               1       25.00  
6                                3       11.11  
24                               1       10.00  
1                                1        9.09  
9                                2        7.69  
0                                2        7.14  
18                               1        6.67  
20                               1        5.56  
27                               1        5.26  
26                               1        4.76

**Worst**:

In [518]:
to_eval_data.sort_values(by = "Percentage", ascending = False).tail(10)

Neighbourhood  Total Restaurants  \
15                                  Forest Hill North                  1   
13                                 Dovercourt Village                  1   
11                                          Deer Park                  4   
10                                         Davisville                 10   
8                                Church and Wellesley                 28   
7                                            Christie                  2   
4                                         Cabbagetown                 11   
3   Business Reply Mail Processing Centre 969 Eastern                  2   
2                                            Brockton                  3   
31                                  The Danforth West                 15   

    Vegetarian / Vegan Restaurants  Percentage  
15                               0         0.0  
13                               0         0.0  
11                               0         0.0  
10                               0         0.0  
8                                0         0.0  
7                                0         0.0  
4                                0         0.0  
3                                0         0.0  
2                                0         0.0  
31                               0         0.0

### Here are the best and worst places in New York to search for a vegetarian/vegan restaurant:

**Best:**

In [519]:
ny_eval_data.sort_values(by = "Percentage", ascending = False).head(10)

Neighbourhood  Total Restaurants  Vegetarian / Vegan Restaurants  \
141              Malba                  1                               1   
245             Utopia                  3                               1   
92       Fresh Meadows                  3                               1   
56        Coney Island                  3                               1   
219      South Jamaica                  3                               1   
100           Grasmere                  4                               1   
71   East Williamsburg                 11                               2   
193    Queensboro Hill                  7                               1   
217               Soho                 20                               2   
31            Bushwick                 20                               2   

     Percentage  
141      100.00  
245       33.33  
92        33.33  
56        33.33  
219       33.33  
100       25.00  
71        18.18  
193       14.29  
217       10.00  
31        10.00

**Worst:**

In [520]:
ny_eval_data.sort_values(by = "Percentage", ascending = False).tail(10)

Neighbourhood  Total Restaurants  Vegetarian / Vegan Restaurants  \
94        Georgetown                  5                               0   
95   Gerritsen Beach                  2                               0   
96         Glen Oaks                  3                               0   
97           Gowanus                 14                               0   
98          Gramercy                 22                               0   
99        Grant City                  6                               0   
101        Gravesend                  3                               0   
102      Great Kills                  7                               0   
105      Grymes Hill                  1                               0   
263        Yorkville                 29                               0   

     Percentage  
94          0.0  
95          0.0  
96          0.0  
97          0.0  
98          0.0  
99          0.0  
101         0.0  
102         0.0  
105         0.0  
263         0.0

### Who of Toronto and New York has now the higher percentage of vegetarian/vegan restaurants?

In [521]:
print("Toronto has {} Vegetarian / Vegan restaurants out of {} total restaurants, which makes up {} %.".format(sum(to_eval_data["Vegetarian / Vegan Restaurants"]), sum(to_eval_data["Total Restaurants"]), 
        round(sum(to_eval_data["Vegetarian / Vegan Restaurants"]) / sum(to_eval_data["Total Restaurants"]) * 100, 2)))

print("New York has {} Vegetarian / Vegan restaurants out of {} total restaurants, which makes up {} %.".format(sum(ny_eval_data["Vegetarian / Vegan Restaurants"]), sum(ny_eval_data["Total Restaurants"]), 
        round(sum(ny_eval_data["Vegetarian / Vegan Restaurants"]) / sum(ny_eval_data["Total Restaurants"]) * 100, 2)))

Toronto has 17 Vegetarian / Vegan restaurants out of 401 total restaurants, which makes up 4.24 %.
New York has 43 Vegetarian / Vegan restaurants out of 2568 total restaurants, which makes up 1.67 %.


# Toronto has a higher percentage of Vegetarian/Vegan restaurants than New York!

### Who of Toronto and New York as a higher density?

In [522]:
to_area = 630 #km^2
ny_area = 790 #km^2
to_pop = 2.62e+6
ny_pop = 8.40e+6

print("Toronto has {} Vegetarian/Vegan restaurants per km$^2$ and {} per million inhabitants.".format(round(sum(to_eval_data["Vegetarian / Vegan Restaurants"])
                                                                                                            / to_area, 2), round(sum(to_eval_data["Vegetarian / Vegan Restaurants"]) / to_pop * 1e+6, 2)))
print("New York has {} Vegetarian/Vegan restaurants per km$^2$ and {} per million inhabitants.".format(round(sum(ny_eval_data["Vegetarian / Vegan Restaurants"])
                                                                                                            / to_area, 2), round(sum(ny_eval_data["Vegetarian / Vegan Restaurants"]) / to_pop * 1e+6, 2)))

Toronto has 0.03 Vegetarian/Vegan restaurants per km$^2$ and 6.49 per million inhabitants.
New York has 0.07 Vegetarian/Vegan restaurants per km$^2$ and 16.41 per million inhabitants.


## New York has a higher vegetarian/vegan restaurant density than Toronto! The lower percentage is due to the fact that New York just has way more restaurants than Toronto!

In [523]:
# The code was removed by Watson Studio for sharing.

'\nplt.style.use("seaborn")\nKs = 6\nmse = np.zeros((Ks-1))\nto_ny_data_clustering = total_eval_data.drop(columns = ["Neighbourhood"])\nfor n in range(1,Ks):\n    \n    # set number of clusters\n    kclusters = n\n    # run k-means clustering\n    kmeans = KMeans(n_clusters=kclusters, random_state=0, init = \'random\', n_init = 10).fit(to_ny_data_clustering)\n    mse[n-1] = kmeans.inertia_\n\nplt.plot(range(1,Ks),mse)\nplt.xlabel("Number of clusters")\nplt.ylabel("MSE")\nplt.title("K selection")\nplt.show()\nnum_klusters = 3\nkmeans = KMeans(n_clusters=num_klusters, random_state=1, init = \'random\', n_init = 15).fit(to_ny_data_clustering)\n    \nto_ny_data_clustering[\'Cluster Labels\'] = kmeans.labels_\n\ntotal_data_clustered = pd.concat([total_eval_data, pd.DataFrame(to_ny_data_clustering["Cluster Labels"])], axis = 1)\ntotal_data_clustered\nto_ny_data_clustering\ntotal_eval_data\nny_df_for_later\ntotal_data_clustered.loc[total_data_clustered[\'Cluster Labels\'] == 0, total_data_clu